In [ ]:
#Author:
#Jinyang Du from NTSG, University of Montana
#12/21/2023

#training ML model for VSM forecasting
#parameters need to be adjusted for 1-w and 2-w forecasts

# Importing the libraries
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import ShuffleSplit
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import LassoCV
from sklearn.datasets import make_regression
from sklearn.feature_selection import SelectFromModel

from sklearn.linear_model import BayesianRidge
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVR
from sklearn.tree import DecisionTreeRegressor

from lightgbm import LGBMRegressor
from xgboost.sklearn import XGBRegressor
from sklearn.linear_model import SGDRegressor
from sklearn.linear_model import ElasticNet
from sklearn.ensemble import GradientBoostingRegressor

from sklearn import preprocessing
from sklearn.preprocessing import Normalizer
from scipy.stats import pearsonr

from sklearn.metrics import explained_variance_score,mean_absolute_error,r2_score
from time import time
from sklearn.linear_model import LinearRegression, Ridge,Lasso
from sklearn.neighbors import KNeighborsRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.ensemble import ExtraTreesRegressor, RandomForestRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.metrics import mean_squared_error

from sklearn.model_selection import cross_val_predict, KFold
from sklearn.metrics import mean_squared_error, r2_score

from joblib import dump, load

import math
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv1D, GlobalMaxPooling1D, Dense
from sklearn.metrics import mean_squared_error

# Read the CSV file into a DataFrame (note: please change the directory as needed)
csvfile='/content/drive/MyDrive/Global_VSM_Forecast/MT_Daily4Forecast_2019_2018_2017_Merge_Interp.csv'
depthStr='10'
#csvfile='/content/drive/MyDrive/Global_VSM_Forecast/MT_Daily4Forecast_2019_2018_2017_Merge_20cm_Interp.csv'
#depthStr='20'
#csvfile='/content/drive/MyDrive/Global_VSM_Forecast/MT_Daily4Forecast_2019_2018_2017_Merge_50cm_Interp.csv'
#depthStr='50'

data0 = pd.read_csv(csvfile,
                   names=["LST_Day_1km","LST_Night_1km",	"NDVI",	"VH",	"VHMedian", \
                          "VV",	"VVMedian", "angle",	"b0",	"b10",	"b100",	"b200",	\
                          "b30",	"b60",	"c01",	"c03",	"c05",	"c07",	"c14", \
                          "doy",	"elevation",	"h01",	"h03",	"h05",	"h07",	\
                          "h14",	"lat",	"lc",	"lon",	"lstDif", \
                          "mTPI",	"p14d",	"p1d",	"p3d",	"p5d",	"p7d",	\
                          "precip14d",	"precip1d",	"precip21d",	"precip28d", \
                          "precip35d",	"precip7d",	"s01",	"s03",	"s05",	"s07",	\
                          "s14",	"slope",	"soil_moisture_am", \
                          "soil_moisture_pm",	"t01",	"t03",	"t05",	"t07",	\
                          "t14",	"u01",	"u03",	"u05",	"u07",	"u14", \
                          "v01",	"v03",	"v05",	"v07",	"v14",	"vsm",	\
                          "vsm14dplus",	"vsm1dplus",	"vsm3dplus", \
                          "vsm5dplus",	"vsm7dplus",	"year","soil_moisture_am_interp", \
                          "soil_moisture_pm_interp"
                          ])


#define feature and target names b30 may be used for the 50-cm forecast
featureNames=["LST_Day_1km","LST_Night_1km",	"NDVI",	"VH", "elevation",\
                          "VV", "b0",	"b10", \
                       #    "b30",
                          "slope", \
                          #"lstDif", \
                          #"mTPI",		\
                          "precip14d",	"precip1d",	"precip21d",	"precip28d", \
                          "precip35d",	"precip7d",	\
                          "s07",	\
                          "h07", \
                          "c07", \
                          "t07",	\
                          "u07", \
                          "p7d", \
                          "v07", \
                          "soil_moisture_pm_interp",
                         # "soil_moisture_am_interp"
                         # "angle"
            ]

targetName="vsm7dplus"
AllFeatures=np.append(featureNames,targetName)
AllFeatures=np.append(AllFeatures,'lat')
AllFeatures=np.append(AllFeatures,'lon')
AllFeatures=np.append(AllFeatures,'angle')
data0=data0[AllFeatures]

print(data0.shape)
for column in featureNames:
  data0[column] = pd.to_numeric(data0[column], errors='coerce')

data0[targetName] = pd.to_numeric(data0[targetName], errors='coerce')

data0.replace([np.inf, -np.inf,-999.0], np.nan, inplace=True) #inplace means data itself will be changed after replacing operation
data0=data0.dropna() #drop the rows with nan
data0[targetName]=data0[targetName]/100.0
data0 = data0[ (data0[targetName] <0.7) & (data0[targetName] >0.01)]
data0 = data0[ (data0['LST_Night_1km'] > 273.15)]


cosval=np.cos(np.radians(pd.to_numeric(data0['angle'])))
data0["VV"]=data0["VV"]/cosval/cosval
data0["VH"]=data0["VH"]/cosval/cosval


model=RandomForestRegressor()
#model=    LGBMRegressor()

# Regularization techniques
model.set_params(n_estimators=50)  # Limit the depth of each tree
model.set_params(max_depth=15)  # Limit the depth of each tree
#model.set_params(min_samples_split=8)  # Set minimum samples required to split a node

model.set_params(min_samples_leaf=5)  # Set minimum samples required at a leaf node
#model.set_params(min_child_samples=5)  # Set minimum samples required at a leaf node

model.set_params(max_features="sqrt")  # Limit the number of features randomly considered
#model.set_params(feature_fraction=0.2)

model.set_params(bootstrap=False)  # Disable bootstrapping

# Create an empty DataFrame to store the normalized data
normalized_df = pd.DataFrame()
ncolumn=data0.shape[1]

X = data0[featureNames]
y = data0[targetName]
X = X.values
y = y.values

num_folds =5
kfold = KFold(n_splits=num_folds, shuffle=True,random_state=42)

# Use a for loop to go through each fold
rmse_scores = np.zeros(num_folds)
r2_scores = np.zeros(num_folds)
r_coor = np.zeros(num_folds)
# Create the cross-validation object
for fold, (train_index, val_index) in enumerate(kfold.split(X, y)):
    X_train, X_test = X[train_index], X[val_index]
    y_train, y_test = y[train_index], y[val_index]

    model.fit(X_train, y_train)
    fold_predictions = model.predict(X_test)

    # Calculate RMSE for the current fold
    rmse_scores[fold] = np.sqrt(mean_squared_error(y_test, fold_predictions))

    # Calculate R^2 score for the current fold
    r2_scores[fold] = r2_score(y_test, fold_predictions)
    r_coor[fold] = pearsonr(y_test, fold_predictions)[0]

    if(r2_scores[fold] <1000.0 ):
      plt.xlabel('Predicted VSM')
      plt.ylabel('Observed VSM')
      plt.plot(fold_predictions,y_test, 'o')
      df = pd.DataFrame({'Original': y_test,  # Optional, replace with your actual data
                   'Predicted': fold_predictions})

    # Print scores for the current fold
    print(f"Fold {fold+1}: RMSE = {rmse_scores[fold]:.3f},  \
    R^2 = {r2_scores[fold]:.3f}, R_Coor = {r_coor[fold]:.3f}")

# Calculate and print the mean scores across all folds
mean_rmse = np.mean(rmse_scores)
mean_r2 = np.mean(r2_scores)
mean_r = np.mean(r_coor)
print("Mean RMSE:", mean_rmse)
print("Mean R^2:", mean_r2)
print("Mean Coor:", mean_r)

model.fit(X, y)
print(X.shape)
xmodel=model

#change the directory as needed
#dump(xmodel, '/content/drive/MyDrive/Global_VSM_Forecast/fore1w_V3_'+depthStr+'cm_interp.joblib')


In [ ]:
#Author:
#Jinyang Du from NTSG, University of Montana
#12/21/2023

#Apply the trained models to multi-band images for forecasting for the Montana region

from joblib import dump, load
from IPython.display import Image as imaging
import numpy as np
import matplotlib.pyplot as plt
import matplotlib as mpl
import folium
import sys

import numpy as np
from osgeo import gdal

#adjust the paths as needed
modelstr='/content/drive/MyDrive/Global_VSM_Forecast/fore1w_V3_10cm_interp.joblib'

instr='/content/drive/MyDrive/Global_VSM_Forecast/images2/MTImage1W_SMAP_M190515.tif'
outstr='/home/MTImage1W_SMAP_M190515_10cm.bin'


clf = load(modelstr)

gdal.UseExceptions()


ds = gdal.Open(instr)

bands = ds.RasterCount

#define feature and target names "b30",
featureNames=["LST_Day_1km","LST_Night_1km",	"NDVI",	"VH", "elevation",\
                          "VV", "b0",	"b10", \
           #               "b30", \
                          "slope", \
                          "precip14d",	"precip1d",	"precip21d",	"precip28d", \
                          "precip35d",	"precip7d",	\
                          "s07",	\
                          "h07", \
                          "c07", \
                          "t07",	\
                          "u07", \
                          "p7d", \
                          "v07", \
                          "soil_moisture_pm_interp",
                         # "soil_moisture_am_interp"
                         # "angle"
            ]

targetName="vsm07dplus"

npredictor=len(featureNames)

#41+1,
bandnum=[ 53+1,40+1,1+1,50+1,0+1,43+1,44+1, \
     #     45+1, \
          51+1,57+1,55+1,58+1,59+1,60+1, \
          56+1,30+1,29+1,31+1,28+1,32+1,8+1,33+1,42+1]


myarrayAng = np.array(ds.GetRasterBand(2+1).ReadAsArray()) #angle band 2+1
cosval=np.cos(np.radians((myarrayAng)))
cosval = np.expand_dims(cosval, 2)


myarray0 = np.array(ds.GetRasterBand(42).ReadAsArray())
myarray0 = np.expand_dims(myarray0, 2)
print(myarray0.shape)
for i in (bandnum):
 # print('working on \n',i)
  myarray = np.array(ds.GetRasterBand(i).ReadAsArray()) #band num starting from 1
  myarray = np.expand_dims(myarray, 2)

  if((i==1+1) or (i==0+1)):
    myarray=myarray/cosval/cosval

  myarray0 = np.concatenate((myarray0, myarray), 2)

print(myarray0.shape)
myarray0=np.nan_to_num(myarray0, nan=-999.0)
print(myarray0.shape)

rgb_img=myarray0
nxall=rgb_img.shape[0]
nyall=rgb_img.shape[1]

a = np.empty(shape=(rgb_img.shape[0]*rgb_img.shape[1], npredictor), dtype=np.float64)

itmp=0
for ax1 in range (0,rgb_img.shape[0]):
  for ax2 in range (0,rgb_img.shape[1]):
    index=ax1*rgb_img.shape[1]+ax2

    xdata=rgb_img[ax1,ax2,0:npredictor]
    a[index,0:npredictor]=xdata

y_predpts = clf.predict(a)


for ax1 in range (0,rgb_img.shape[0]):
  for ax2 in range (0,rgb_img.shape[1]):
    index=ax1*rgb_img.shape[1]+ax2
    xdata=rgb_img[ax1,ax2,0:npredictor]
    if(np.amin(xdata)<-100.0):
      y_predpts[index]=-999.0
    else:
      itmp=itmp+1
      if(itmp == 10):
        print(xdata,' and ',y_predpts[index])

tmparray=y_predpts.reshape(nxall,nyall) #besure to check the dimensions!!!!!
plt.imshow(tmparray)
plt.show()
tmparray=y_predpts.reshape(nyall,nxall)

file = open(outstr, "wb")
file.write(tmparray)
file.close()
